In [1]:
import torch
import torch_geometric
import torch_scatter
import torch_sparse
import torch_cluster
import torch_spline_conv

print("✅ All PyG packages imported successfully!")


✅ All PyG packages imported successfully!


In [2]:
import torch
import numpy as np
from deeprobust.graph.data import Dataset
from deeprobust.graph.defense import GCN
from deeprobust.graph.global_attack import Metattack

data = Dataset(root='/tmp/', name='citeseer', setting='nettack')
adj, features, labels = data.adj, data.features, data.labels
idx_train, idx_val, idx_test = data.idx_train, data.idx_val, data.idx_test
idx_unlabeled = np.union1d(idx_val, idx_test)

Loading citeseer dataset...
Selecting 1 largest connected components


In [3]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
surrogate = GCN(nfeat=features.shape[1], nclass=labels.max().item()+1, nhid=64,
                with_relu=False, device=device)
surrogate = surrogate.to(device)
surrogate.fit(features, adj, labels, idx_train)

original_adj_dense = adj.copy()

/home/niyati/miniconda3/envs/ersp_v2/lib/python3.9/site-packages/deeprobust/graph/utils.py:356: UserWarning: torch.sparse.SparseTensor(indices, values, shape, *, device=) is deprecated.  Please use torch.sparse_coo_tensor(indices, values, shape, dtype=, device=). (Triggered internally at /pytorch/torch/csrc/utils/tensor_new.cpp:644.)
  return torch.sparse.FloatTensor(sparseconcat.t(),sparsedata,torch.Size(sparse_mx.shape))


In [4]:
# Initialize dictionaries to track edge frequencies
added_edge_counts = {}
removed_edge_counts = {}
perturbed_edge_counts = {}  # Combined tracking for any perturbation

for iteration in range(5):
    surrogate = GCN(nfeat=features.shape[1], nclass=labels.max().item()+1, nhid=64,
                with_relu=False, device=device)
    surrogate = surrogate.to(device)
    surrogate.fit(features, adj, labels, idx_train)
    model = Metattack(model=surrogate, nnodes=adj.shape[0], feature_shape=features.shape, device=device)
    model = model.to(device)
    perturbations = int(1.00 * (adj.sum() // 2))
    model.attack(features, adj, labels, idx_train, idx_unlabeled, perturbations, ll_constraint=False)
    modified_adj = model.modified_adj
    
    # Convert modified adjacency tensor to numpy for comparison
    if isinstance(modified_adj, torch.Tensor):
        modified_adj_dense = modified_adj.cpu().numpy()
    else:
        modified_adj_dense = modified_adj.todense()
    
    # Find added and removed edges
    iteration_added_edges = []
    iteration_removed_edges = []
    
    for i in range(adj.shape[0]):
        for j in range(i + 1, adj.shape[0]):
            # Check if edge was added (wasn't in original but is in modified)
            if original_adj_dense[i, j] == 0 and modified_adj_dense[i, j] != 0:
                edge = (i, j)
                iteration_added_edges.append(edge)
                # Update frequency count for this edge
                added_edge_counts[edge] = added_edge_counts.get(edge, 0) + 1
                perturbed_edge_counts[edge] = perturbed_edge_counts.get(edge, 0) + 1
            
            # Check if edge was removed (was in original but not in modified)
            elif original_adj_dense[i, j] != 0 and modified_adj_dense[i, j] == 0:
                edge = (i, j)
                iteration_removed_edges.append(edge)
                # Update frequency count for this edge
                removed_edge_counts[edge] = removed_edge_counts.get(edge, 0) + 1
                perturbed_edge_counts[edge] = perturbed_edge_counts.get(edge, 0) + 1
    
    # Combine lists for this iteration
    iteration_perturbed_edges = iteration_added_edges + iteration_removed_edges
    
    print(f"Iteration {iteration}:")
    print(f"  Added edges: {len(iteration_added_edges)}")
    print(f"  Removed edges: {len(iteration_removed_edges)}")
    print(f"  Total perturbed edges: {len(iteration_perturbed_edges)}")
    print(f"  Sample perturbed edges: {iteration_perturbed_edges[:5] if iteration_perturbed_edges else 'None'}")

# Sort all edges by frequency (highest to lowest)
sorted_perturbed_edges = sorted(perturbed_edge_counts.items(), key=lambda x: x[1], reverse=True)
sorted_added_edges = sorted(added_edge_counts.items(), key=lambda x: x[1], reverse=True)
sorted_removed_edges = sorted(removed_edge_counts.items(), key=lambda x: x[1], reverse=True)


# Count edges by frequency
perturbation_frequency_distribution = {}
for count in perturbed_edge_counts.values():
    perturbation_frequency_distribution[count] = perturbation_frequency_distribution.get(count, 0) + 1

print("\nPerturbation frequency distribution (times_perturbed, num_edges):")
for count, num_edges in sorted(perturbation_frequency_distribution.items()):
    print(f"  Perturbed {count} times: {num_edges} edges")

# Calculate edge consistency across iterations
print(f"\nTotal unique edges perturbed across all iterations: {len(perturbed_edge_counts)}")
print(f"Edges perturbed in all iterations: {sum(1 for count in perturbed_edge_counts.values() if count == 5)}")

Perturbing graph:   0%|                                                                        | 0/3668 [00:00<?, ?it/s]

GCN loss on unlabled data: 1.1028220653533936
GCN acc on unlabled data: 0.7309110057925223
attack loss: 0.16463042795658112


Perturbing graph:   0%|                                                              | 1/3668 [00:01<1:47:37,  1.76s/it]

GCN loss on unlabled data: 1.0991090536117554
GCN acc on unlabled data: 0.7298578199052133
attack loss: 0.16838455200195312


Perturbing graph:   0%|                                                              | 2/3668 [00:02<1:01:55,  1.01s/it]

...

Perturbing graph: 100%|████████████████████████████████████████████████████████████▉| 3667/3668 [26:08<00:00,  2.82it/s]

GCN loss on unlabled data: 13.58253288269043
GCN acc on unlabled data: 0.06951026856240126
attack loss: 7.092310428619385


Perturbing graph: 100%|█████████████████████████████████████████████████████████████| 3668/3668 [26:08<00:00,  2.34it/s]

GCN loss on unlabled data: 13.407719612121582
GCN acc on unlabled data: 0.06635071090047392
attack loss: 7.002811431884766


Iteration 4:
  Added edges: 3514
  Removed edges: 154
  Total perturbed edges: 3668
  Sample perturbed edges: [(0, 364), (2, 1377), (2, 1909), (3, 857), (3, 1164)]

Perturbation frequency distribution (times_perturbed, num_edges):
  Perturbed 1 times: 15455 edges
  Perturbed 2 times: 907 edges
  Perturbed 3 times: 141 edges
  Perturbed 4 times: 82 edges
  Perturbed 5 times: 64 edges

Total unique edges perturbed across all iterations: 16649
Edges perturbed in all iterations: 64


In [5]:
import os
save_path = os.path.join(os.getcwd(), "GreedyAggregated_Citeseer_edges_list.pth")
torch.save(sorted_perturbed_edges, save_path)


In [9]:
print(len(perturbed_edge_counts))
#print(budget)

130


In [16]:
rm -rf ./Cora

In [27]:
sys.path.append(os.path.abspath("../../"))
from torch.serialization import safe_globals
from torch_geometric.data import Data
from src.models.gcn import *
from src.utils.datasets import *
from src.models.trainable import *
from src.attacks.greedy_gd import *


# Allow torch.load to unpickle PyG's Data object
with safe_globals([Data]):
    from torch_geometric.datasets import Planetoid
    import torch

    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    cora_dataset = Planetoid(root='.', name='Cora')
    data = cora_dataset[0].to(device)
    print(data)

model = GCN(data.x.shape[1], cora_dataset.num_classes, [64]).to(device)

model.reset_parameters()
train = Trainable(model)
train.fit(data, 200)

initial_loss, initial_accuracy = train.test(data)
print(f"Initial Accuracy: {initial_accuracy}")
print(f"Initial Loss: {initial_loss}")

G = to_networkx(data, to_undirected=True)
initial_edge_count = G.number_of_edges() // 2
ptb_rate = 0.20
budget = int(ptb_rate * initial_edge_count)

Data(x=[2708, 1433], edge_index=[2, 10556], y=[2708], train_mask=[2708], val_mask=[2708], test_mask=[2708])
Epoch 0, Train Loss - 1.9513059854507446, Val Loss - 1.8159871101379395, Val Accuracy - 0.673
Epoch 20, Train Loss - 0.015081415884196758, Val Loss - 0.6655123233795166, Val Accuracy - 0.792
Epoch 40, Train Loss - 0.0073927463963627815, Val Loss - 0.6706228852272034, Val Accuracy - 0.791
Epoch 60, Train Loss - 0.011818666942417622, Val Loss - 0.6108243465423584, Val Accuracy - 0.81
Epoch 80, Train Loss - 0.014592904597520828, Val Loss - 0.6196398138999939, Val Accuracy - 0.806
Epoch 100, Train Loss - 0.016452601179480553, Val Loss - 0.6524885892868042, Val Accuracy - 0.798
Epoch 120, Train Loss - 0.010858620516955853, Val Loss - 0.6451842188835144, Val Accuracy - 0.804
Epoch 140, Train Loss - 0.009836899116635323, Val Loss - 0.6186845898628235, Val Accuracy - 0.816
Epoch 160, Train Loss - 0.009267968125641346, Val Loss - 0.649171769618988, Val Accuracy - 0.805
Epoch 180, Train Lo

In [30]:
from src.attacks.greedy_gd import Metattack as MyMetattack
def two_phase_attack(split):
    diff_threshold = 0.01
    first_phase_edges = int(budget * split)
    second_phase_percent = ptb_rate * (1 - split) * 0.5
    print(f"\n--- Running split: {split} ---")
    print(f"Second phase perturbation rate: {second_phase_percent:.4f}")

    phase1_accuracies = []
    phase2_accuracies = []

    G = to_networkx(data, to_undirected=True)
    data_copy = copy.copy(data)

    i, j = 0, 0  # i - edges successfully added, j - index in list

    # === Phase 1 ===
    while i < first_phase_edges:
        if j >= len(all_perturbed_edges):
            print("Ran out of candidate edges in Phase 1. Moving to Phase 2.")
            break

        u, v = all_perturbed_edges[j]
        G.add_edge(u, v)

        modified_data = from_networkx(G).to(device)
        modified_data.x = data.x 
        modified_data.y = data.y 
        modified_data.train_mask = data.train_mask
        modified_data.test_mask = data.test_mask

        _, modified_accuracy = train.test(modified_data)

        if modified_accuracy == initial_accuracy:
            i += 1
            phase1_accuracies.append(modified_accuracy)
        else:
            G.remove_edge(u, v)

        j += 1

    print(f"Phase 1: Added {i} edges out of requested {first_phase_edges}.")

    # === Phase 2 ===
    modified_data = from_networkx(G).to(device)
    modified_data.x = data.x 
    modified_data.y = data.y 
    modified_data.train_mask = data.train_mask
    modified_data.test_mask = data.test_mask

    attacker = MyMetattack(modified_data, device=device)
    attacker.setup_surrogate(model,
                             labeled_nodes=data.train_mask,
                             unlabeled_nodes=data.test_mask, 
                             lambda_=0.)
    attacker.reset()
    attacker.attack(second_phase_percent)

    degs = defaultdict(tuple)
    for k, v in attacker._added_edges.items():
        degs[v] = (k, True)
    for k, v in attacker._removed_edges.items():
        degs[v] = (k, False)

    for _, second in degs.items():
        u, v = second[0]
        if second[1]:
            G.add_edge(u, v)
        else:
            G.remove_edge(u, v)

        modified_data = from_networkx(G).to(device)
        modified_data.x = data.x 
        modified_data.y = data.y 
        modified_data.train_mask = data.train_mask
        modified_data.test_mask = data.test_mask

        _, modified_accuracy = train.test(modified_data)
        phase2_accuracies.append(modified_accuracy)

    # === Final Reporting ===
    final_accuracy = phase2_accuracies[-1] if phase2_accuracies else (
        phase1_accuracies[-1] if phase1_accuracies else initial_accuracy)
    accuracy_drop = initial_accuracy - final_accuracy

    print(f"Final Accuracy: {final_accuracy:.4f}")
    print(f"Accuracy Drop: {accuracy_drop:.4f}")

    return {
        "split": split,
        "phase1_added": i,
        "phase1_accuracies": phase1_accuracies,
        "phase2_accuracies": phase2_accuracies,
        "final_accuracy": final_accuracy,
        "accuracy_drop": accuracy_drop
    }


In [31]:
splits = [0, 0.5]
split_dic = defaultdict(dict)
for s in splits:
    split_dic[s] = two_phase_attack(s)


--- Running split: 0 ---
Second phase perturbation rate: 0.1000
Phase 1: Added 0 edges out of requested 0.


Peturbing graph...:   0%|          | 0/527 [00:00<?, ?it/s]

RuntimeError: [enforce fail at alloc_cpu.cpp:118] err == 0. DefaultCPUAllocator: can't allocate memory: you tried to allocate 79404582592 bytes. Error code 12 (Cannot allocate memory)